In [ ]:
import json

# Load the dataset
with open('Counterspeech_Dataset.json', 'r') as file:
    dataset = json.load(file)

# Create a new transformed dataset
transformed_dataset = []

def community_mapper(community):
    """Function to convert community names."""
    mapping = {
        "jews": "Jewish",
        "black": "Black",
        "lgbt": "LGBT"
    }
    return mapping.get(community, community) # returns the community name if it's not in the dictionary

for entry in dataset:
    # Check if necessary keys are in the entry
    if "Community" in entry and "commentText" in entry and "CounterSpeech" in entry:
        community_name = community_mapper(entry["Community"])
        transformed_entry = {
            "Prompt": f'A YouTube Video, which contains hateful content that targets the {community_name} community, has the following comment: {entry["commentText"]}',
            "CounterSpeech": entry["CounterSpeech"] # enclosing the value in double quotes
        }
        transformed_dataset.append(transformed_entry)

# Save the transformed dataset to a new JSON file
with open('Transformed_Counterspeech_Dataset.json', 'w') as file:
    json.dump(transformed_dataset, file, indent=4)


In [ ]:
with open("Transformed_Counterspeech_Dataset.json", "r") as file:
    data = json.load(file)

# Prepare the transformed data
transformed_data = []

system_message = "You are an assistant that is meant to determine whether the comment mentioned in the user message is an example of counterspeech. Counterspeech is defined as a response or comment that counters hateful or harmful speech/ideas. Respond with true or false."

for entry in data:
    user_message_content = entry["Prompt"]
    assistant_message_content = "true" if entry["CounterSpeech"] else "false"

    message_group = {
        "messages": [
            {"role": "system", "content": system_message},
            {"role": "user", "content": user_message_content},
            {"role": "assistant", "content": assistant_message_content}
        ]
    }

    transformed_data.append(message_group)

# Save the transformed data to a new JSONL file
with open("transformed_data.jsonl", "w") as file:
    for item in transformed_data:
        json.dump(item, file)
        file.write("\n")

In [ ]:
import json
from sklearn.model_selection import train_test_split

# Load the data from jsonl file
with open('transformed_data.jsonl', 'r') as file:
    data = [json.loads(line) for line in file]

# Extract labels from data
labels = [entry['messages'][2]['content'] for entry in data]

# Split the data using stratified sampling to maintain the class balance
train_data, temp_data, train_labels, temp_labels = train_test_split(data, labels, test_size=0.2, stratify=labels)
valid_data, test_data, valid_labels, test_labels = train_test_split(temp_data, temp_labels, test_size=0.5, stratify=temp_labels)

# Save split data to separate jsonl files
with open('train_data.jsonl', 'w') as file:
    for item in train_data:
        file.write(json.dumps(item) + '\n')

with open('valid_data.jsonl', 'w') as file:
    for item in valid_data:
        file.write(json.dumps(item) + '\n')

with open('test_data.jsonl', 'w') as file:
    for item in test_data:
        file.write(json.dumps(item) + '\n')


In [ ]:
# We start by importing the required packages

import json
import os
import tiktoken
import numpy as np
from collections import defaultdict

# Next, we specify the data path and open the JSONL file

data_path = "train_data.jsonl"

# Load dataset
with open(data_path) as f:
    dataset = [json.loads(line) for line in f]

# We can inspect the data quickly by checking the number of examples and the first item

# Initial dataset stats
print("Num examples:", len(dataset))
print("First example:")
for message in dataset[0]["messages"]:
    print(message)

# Now that we have a sense of the data, we need to go through all the different examples and check to make sure the formatting is correct and matches the Chat completions message structure

# Format error checks
format_errors = defaultdict(int)

for ex in dataset:
    if not isinstance(ex, dict):
        format_errors["data_type"] += 1
        continue

    messages = ex.get("messages", None)
    if not messages:
        format_errors["missing_messages_list"] += 1
        continue

    for message in messages:
        if "role" not in message or "content" not in message:
            format_errors["message_missing_key"] += 1

        if any(k not in ("role", "content", "name") for k in message):
            format_errors["message_unrecognized_key"] += 1

        if message.get("role", None) not in ("system", "user", "assistant"):
            format_errors["unrecognized_role"] += 1

        content = message.get("content", None)
        if not content or not isinstance(content, str):
            format_errors["missing_content"] += 1

    if not any(message.get("role", None) == "assistant" for message in messages):
        format_errors["example_missing_assistant_message"] += 1

if format_errors:
    print("Found errors:")
    for k, v in format_errors.items():
        print(f"{k}: {v}")
else:
    print("No errors found")

# Beyond the structure of the message, we also need to ensure that the length does not exceed the 4096 token limit.

# Token counting functions
encoding = tiktoken.get_encoding("cl100k_base")

# not exact!
# simplified from https://github.com/openai/openai-cookbook/blob/main/examples/How_to_count_tokens_with_tiktoken.ipynb
def num_tokens_from_messages(messages, tokens_per_message=3, tokens_per_name=1):
    num_tokens = 0
    for message in messages:
        num_tokens += tokens_per_message
        for key, value in message.items():
            num_tokens += len(encoding.encode(value))
            if key == "name":
                num_tokens += tokens_per_name
    num_tokens += 3
    return num_tokens

def num_assistant_tokens_from_messages(messages):
    num_tokens = 0
    for message in messages:
        if message["role"] == "assistant":
            num_tokens += len(encoding.encode(message["content"]))
    return num_tokens

def print_distribution(values, name):
    print(f"\n#### Distribution of {name}:")
    print(f"min / max: {min(values)}, {max(values)}")
    print(f"mean / median: {np.mean(values)}, {np.median(values)}")
    print(f"p5 / p95: {np.quantile(values, 0.1)}, {np.quantile(values, 0.9)}")

# Last, we can look at the results of the different formatting operations before proceeding with creating a fine-tuning job:

# Warnings and tokens counts
n_missing_system = 0
n_missing_user = 0
n_messages = []
convo_lens = []
assistant_message_lens = []

for ex in dataset:
    messages = ex["messages"]
    if not any(message["role"] == "system" for message in messages):
        n_missing_system += 1
    if not any(message["role"] == "user" for message in messages):
        n_missing_user += 1
    n_messages.append(len(messages))
    convo_lens.append(num_tokens_from_messages(messages))
    assistant_message_lens.append(num_assistant_tokens_from_messages(messages))

print("Num examples missing system message:", n_missing_system)
print("Num examples missing user message:", n_missing_user)
print_distribution(n_messages, "num_messages_per_example")
print_distribution(convo_lens, "num_total_tokens_per_example")
print_distribution(assistant_message_lens, "num_assistant_tokens_per_example")
n_too_long = sum(l > 4096 for l in convo_lens)
print(f"\n{n_too_long} examples may be over the 4096 token limit, they will be truncated during fine-tuning")

# Pricing and default n_epochs estimate
MAX_TOKENS_PER_EXAMPLE = 4096

MIN_TARGET_EXAMPLES = 100
MAX_TARGET_EXAMPLES = 25000
TARGET_EPOCHS = 3
MIN_EPOCHS = 1
MAX_EPOCHS = 25

n_epochs = TARGET_EPOCHS
n_train_examples = len(dataset)
if n_train_examples * TARGET_EPOCHS < MIN_TARGET_EXAMPLES:
    n_epochs = min(MAX_EPOCHS, MIN_TARGET_EXAMPLES // n_train_examples)
elif n_train_examples * TARGET_EPOCHS > MAX_TARGET_EXAMPLES:
    n_epochs = max(MIN_EPOCHS, MAX_TARGET_EXAMPLES // n_train_examples)

n_billing_tokens_in_dataset = sum(min(MAX_TOKENS_PER_EXAMPLE, length) for length in convo_lens)
print(f"Dataset has ~{n_billing_tokens_in_dataset} tokens that will be charged for during training")
print(f"By default, you'll train for {n_epochs} epochs on this dataset")
print(f"By default, you'll be charged for ~{n_epochs * n_billing_tokens_in_dataset} tokens")
print("See pricing page to estimate total costs")

Num examples: 11137
First example:
{'role': 'system', 'content': 'You are an assistant that is meant to determine whether the comment mentioned in the user message is an example of counterspeech. Counterspeech is defined as a response or comment that counters hateful or harmful speech/ideas. Respond with true or false.'}
{'role': 'user', 'content': 'A YouTube Video, which contains hateful content that targets the Jewish community, has the following comment: wtf how many times has Allah mentioned he is the last messenger and is a blueprint for the future etc etc\nu hheard of the shahadah? \n34.28 - messenger \n33.40 - confirms this \n\nnot sure about adam not done my research yet\nlet me know ure response'}
{'role': 'assistant', 'content': 'false'}
No errors found
Num examples missing system message: 0
Num examples missing user message: 0

#### Distribution of num_messages_per_example:
min / max: 3, 3
mean / median: 3.0, 3.0
p5 / p95: 3.0, 3.0

#### Distribution of num_total_tokens_per_

In [ ]:
!pip install openai

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.5/76.5 kB 1.8 MB/s eta 0:00:00


In [ ]:
import os

os.environ["OPENAI_API_KEY"] =<insert OpenAI API Key>

In [ ]:
import openai
import os
openai.api_key = os.environ.get("OPENAI_API_KEY")

openai.File.create(
  file=open("train_data.jsonl", "rb"),
  purpose='fine-tune'
)

<File file id=file-uds0e4OPxC80ZseqbKW9g72d at 0x796934c44720> JSON: {
  "object": "file",
  "id": "file-uds0e4OPxC80ZseqbKW9g72d",
  "purpose": "fine-tune",
  "filename": "file",
  "bytes": 7647765,
  "created_at": 1693539133,
  "status": "uploaded",
  "status_details": null
}

In [ ]:
openai.FineTuningJob.create(training_file="file-Pw3EojvRsi5mcITwyn9bIDKw", model="gpt-3.5-turbo")

<FineTuningJob fine_tuning.job id=ftjob-cbubgF9qMnGGqhcuCIWRiSWu at 0x7969234f7420> JSON: {
  "object": "fine_tuning.job",
  "id": "ftjob-cbubgF9qMnGGqhcuCIWRiSWu",
  "model": "gpt-3.5-turbo-0613",
  "created_at": 1693539140,
  "finished_at": null,
  "fine_tuned_model": null,
  "organization_id": "org-8EdgLmZyodOaLJc4scfYYceO",
  "result_files": [],
  "status": "created",
  "validation_file": null,
  "training_file": "file-Pw3EojvRsi5mcITwyn9bIDKw",
  "hyperparameters": {
    "n_epochs": 2
  },
  "trained_tokens": null
}

In [ ]:
openai.FineTuningJob.retrieve("ftjob-cbubgF9qMnGGqhcuCIWRiSWu")

<FineTuningJob fine_tuning.job id=ftjob-cbubgF9qMnGGqhcuCIWRiSWu at 0x796934cddf80> JSON: {
  "object": "fine_tuning.job",
  "id": "ftjob-cbubgF9qMnGGqhcuCIWRiSWu",
  "model": "gpt-3.5-turbo-0613",
  "created_at": 1693539140,
  "finished_at": null,
  "fine_tuned_model": null,
  "organization_id": "org-8EdgLmZyodOaLJc4scfYYceO",
  "result_files": [],
  "status": "running",
  "validation_file": null,
  "training_file": "file-Pw3EojvRsi5mcITwyn9bIDKw",
  "hyperparameters": {
    "n_epochs": 2
  },
  "trained_tokens": null
}

In [ ]:
!pip install openai

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.5/76.5 kB 988.3 kB/s eta 0:00:00


In [ ]:
import openai
import os

os.environ["OPENAI_API_KEY"] =<Insert API Key>

openai.api_key = os.environ.get("OPENAI_API_KEY")

openai.FineTuningJob.retrieve("ftjob-cbubgF9qMnGGqhcuCIWRiSWu")

<FineTuningJob fine_tuning.job id=ftjob-cbubgF9qMnGGqhcuCIWRiSWu at 0x7cd895c1ce50> JSON: {
  "object": "fine_tuning.job",
  "id": "ftjob-cbubgF9qMnGGqhcuCIWRiSWu",
  "model": "gpt-3.5-turbo-0613",
  "created_at": 1693539140,
  "finished_at": 1693541905,
  "fine_tuned_model": "ft:gpt-3.5-turbo-0613:personal::7tptzfbo",
  "organization_id": "org-8EdgLmZyodOaLJc4scfYYceO",
  "result_files": [
    "file-UVOtPhw6xwwLOOjzQr8vQcly"
  ],
  "status": "succeeded",
  "validation_file": null,
  "training_file": "file-Pw3EojvRsi5mcITwyn9bIDKw",
  "hyperparameters": {
    "n_epochs": 2
  },
  "trained_tokens": 2831224
}

In [ ]:
import openai
import json
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score

# Load the validation data
with open("valid_data.jsonl", "r") as f:
    valid_data = [json.loads(line) for line in f]

# Initialize the lists for true labels and predictions
true_labels = []
predicted_labels = []

# Get predictions for each example in validation data
for example in valid_data:
    completion = openai.ChatCompletion.create(
        model="ft:gpt-3.5-turbo-0613:personal::7tptzfbo",
        messages=[
            {"role": "system", "content": "You are an assistant that is meant to determine whether the comment mentioned in the user message is an example of counterspeech. Counterspeech is defined as a response or comment that counters hateful or harmful speech/ideas. Respond with true or false."},
            {"role": "user", "content": example["messages"][1]["content"]}
        ]
    )

    predicted = completion.choices[0].message["content"].lower()
    true = example["messages"][2]["content"].lower()

    predicted_labels.append(predicted)
    true_labels.append(true)

# Calculate evaluation metrics
accuracy = accuracy_score(true_labels, predicted_labels)
precision = precision_score(true_labels, predicted_labels, pos_label="true")
recall = recall_score(true_labels, predicted_labels, pos_label="true")
f1 = f1_score(true_labels, predicted_labels, pos_label="true")

# Find which examples were incorrect
incorrect_examples = [example for i, example in enumerate(valid_data) if true_labels[i] != predicted_labels[i]]
correct_examples = [example for i, example in enumerate(valid_data) if true_labels[i] == predicted_labels[i]]

# Print the results
print(f"Accuracy: {accuracy:.2f}")
print(f"Precision: {precision:.2f}")
print(f"Recall: {recall:.2f}")
print(f"F1-score: {f1:.2f}")
print("\nIncorrect Examples:")
for example in incorrect_examples:
    print(example)
print("\nCorrect Examples:")
for example in correct_examples:
    print(example)


Accuracy: 0.82
Precision: 0.82
Recall: 0.81
F1-score: 0.82

Incorrect Examples:
{'messages': [{'role': 'system', 'content': 'You are an assistant that is meant to determine whether the comment mentioned in the user message is an example of counterspeech. Counterspeech is defined as a response or comment that counters hateful or harmful speech/ideas. Respond with true or false.'}, {'role': 'user', 'content': "A YouTube Video, which contains hateful content that targets the Jewish community, has the following comment: Easy.  Marx, and for that matter Mussolini were both writers and believers in leftist thought.  Marx, however, was not a fascist.  Mussolini was a fascist. . . The problem with your argument is the fact that you think that fascism, by definition, is a manifestation of the right, but it's not.  There are fascists on both sides.  Just because someone isn't shoving a gun in your face, making you do something or the other, doesn't invalidate their clear fascism.  Go back and li

In [ ]:
# Creating a new fine tuning model with 4 epochs
import openai
import os
openai.api_key = os.environ.get("OPENAI_API_KEY")

openai.File.create(
  file=open("train_data.jsonl", "rb"),
  purpose='fine-tune'
)

<File file id=file-ks0IQ1oFKSbEsYtqitPIfcTf at 0x7cd8957f16c0> JSON: {
  "object": "file",
  "id": "file-ks0IQ1oFKSbEsYtqitPIfcTf",
  "purpose": "fine-tune",
  "filename": "file",
  "bytes": 7647765,
  "created_at": 1693573162,
  "status": "uploaded",
  "status_details": null
}

In [ ]:
openai.FineTuningJob.create(training_file="file-ks0IQ1oFKSbEsYtqitPIfcTf", model="gpt-3.5-turbo", hyperparameters={"n_epochs": 4})

<FineTuningJob fine_tuning.job id=ftjob-tVW52S3qC5Vfvh5NgYaSSBmW at 0x7cd8825679c0> JSON: {
  "object": "fine_tuning.job",
  "id": "ftjob-tVW52S3qC5Vfvh5NgYaSSBmW",
  "model": "gpt-3.5-turbo-0613",
  "created_at": 1693573869,
  "finished_at": null,
  "fine_tuned_model": null,
  "organization_id": "org-8EdgLmZyodOaLJc4scfYYceO",
  "result_files": [],
  "status": "created",
  "validation_file": null,
  "training_file": "file-ks0IQ1oFKSbEsYtqitPIfcTf",
  "hyperparameters": {
    "n_epochs": 4
  },
  "trained_tokens": null
}

In [ ]:
# List 10 fine-tuning jobs
openai.FineTuningJob.list(limit=10)

<OpenAIObject list at 0x7cd8957b0a90> JSON: {
  "object": "list",
  "data": [
    {
      "object": "fine_tuning.job",
      "id": "ftjob-tVW52S3qC5Vfvh5NgYaSSBmW",
      "model": "gpt-3.5-turbo-0613",
      "created_at": 1693573869,
      "finished_at": null,
      "fine_tuned_model": null,
      "organization_id": "org-8EdgLmZyodOaLJc4scfYYceO",
      "result_files": [],
      "status": "running",
      "validation_file": null,
      "training_file": "file-ks0IQ1oFKSbEsYtqitPIfcTf",
      "hyperparameters": {
        "n_epochs": 4
      },
      "trained_tokens": null
    },
    {
      "object": "fine_tuning.job",
      "id": "ftjob-cbubgF9qMnGGqhcuCIWRiSWu",
      "model": "gpt-3.5-turbo-0613",
      "created_at": 1693539140,
      "finished_at": 1693541905,
      "fine_tuned_model": "ft:gpt-3.5-turbo-0613:personal::7tptzfbo",
      "organization_id": "org-8EdgLmZyodOaLJc4scfYYceO",
      "result_files": [
        "file-UVOtPhw6xwwLOOjzQr8vQcly"
      ],
      "status": "succeeded"

In [ ]:
# List up to 10 events from a fine-tuning job
openai.FineTuningJob.list_events(id="ftjob-tVW52S3qC5Vfvh5NgYaSSBmW", limit=10)

<OpenAIObject list at 0x7cd881e72660> JSON: {
  "object": "list",
  "data": [
    {
      "object": "fine_tuning.job.event",
      "id": "ftevent-WT2md6dC6MQW5bKbfAkDSp4Z",
      "created_at": 1693576313,
      "level": "info",
      "message": "Fine-tuning job successfully completed",
      "data": null,
      "type": "message"
    },
    {
      "object": "fine_tuning.job.event",
      "id": "ftevent-Z6nu64aLAUdVnQcjULN3GXmK",
      "created_at": 1693576312,
      "level": "info",
      "message": "New fine-tuned model created: ft:gpt-3.5-turbo-0613:personal::7tyqtmxH",
      "data": null,
      "type": "message"
    },
    {
      "object": "fine_tuning.job.event",
      "id": "ftevent-eYcSDHiUy2oUETvYfa7qBWC3",
      "created_at": 1693576262,
      "level": "info",
      "message": "Step 1500/1537: training loss=0.04",
      "data": {
        "step": 1500,
        "train_loss": 0.0354250930249691,
        "train_mean_token_accuracy": 0.9885057210922241
      },
      "type": "metri

In [ ]:
openai.FineTuningJob.retrieve("ftjob-tVW52S3qC5Vfvh5NgYaSSBmW")

<FineTuningJob fine_tuning.job id=ftjob-tVW52S3qC5Vfvh5NgYaSSBmW at 0x7cd881e62c50> JSON: {
  "object": "fine_tuning.job",
  "id": "ftjob-tVW52S3qC5Vfvh5NgYaSSBmW",
  "model": "gpt-3.5-turbo-0613",
  "created_at": 1693573869,
  "finished_at": 1693576310,
  "fine_tuned_model": "ft:gpt-3.5-turbo-0613:personal::7tyqtmxH",
  "organization_id": "org-8EdgLmZyodOaLJc4scfYYceO",
  "result_files": [
    "file-kJvCcDsjFgAipqOQo1a3gcTc"
  ],
  "status": "succeeded",
  "validation_file": null,
  "training_file": "file-ks0IQ1oFKSbEsYtqitPIfcTf",
  "hyperparameters": {
    "n_epochs": 4
  },
  "trained_tokens": 5662448
}

In [ ]:
import openai
import json
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score

# Load the validation data
with open("valid_data.jsonl", "r") as f:
    valid_data = [json.loads(line) for line in f]

# Initialize the lists for true labels and predictions
true_labels = []
predicted_labels = []

# Get predictions for each example in validation data
for example in valid_data:
    completion = openai.ChatCompletion.create(
        model="ft:gpt-3.5-turbo-0613:personal::7tyqtmxH",
        messages=[
            {"role": "system", "content": "You are an assistant that is meant to determine whether the comment mentioned in the user message is an example of counterspeech. Counterspeech is defined as a response or comment that counters hateful or harmful speech/ideas. Respond with true or false."},
            {"role": "user", "content": example["messages"][1]["content"]}
        ]
    )

    predicted = completion.choices[0].message["content"].lower()
    true = example["messages"][2]["content"].lower()

    predicted_labels.append(predicted)
    true_labels.append(true)

# Calculate evaluation metrics
accuracy = accuracy_score(true_labels, predicted_labels)
precision = precision_score(true_labels, predicted_labels, pos_label="true")
recall = recall_score(true_labels, predicted_labels, pos_label="true")
f1 = f1_score(true_labels, predicted_labels, pos_label="true")

# Find which examples were incorrect
incorrect_examples = [example for i, example in enumerate(valid_data) if true_labels[i] != predicted_labels[i]]
correct_examples = [example for i, example in enumerate(valid_data) if true_labels[i] == predicted_labels[i]]

# Print the results
print(f"Accuracy: {accuracy:.2f}")
print(f"Precision: {precision:.2f}")
print(f"Recall: {recall:.2f}")
print(f"F1-score: {f1:.2f}")
print("\nIncorrect Examples:")
for example in incorrect_examples:
    print(example)
print("\nCorrect Examples:")
for example in correct_examples:
    print(example)


Accuracy: 0.85
Precision: 0.85
Recall: 0.84
F1-score: 0.85

Incorrect Examples:
{'messages': [{'role': 'system', 'content': 'You are an assistant that is meant to determine whether the comment mentioned in the user message is an example of counterspeech. Counterspeech is defined as a response or comment that counters hateful or harmful speech/ideas. Respond with true or false.'}, {'role': 'user', 'content': "A YouTube Video, which contains hateful content that targets the Jewish community, has the following comment: Easy.  Marx, and for that matter Mussolini were both writers and believers in leftist thought.  Marx, however, was not a fascist.  Mussolini was a fascist. . . The problem with your argument is the fact that you think that fascism, by definition, is a manifestation of the right, but it's not.  There are fascists on both sides.  Just because someone isn't shoving a gun in your face, making you do something or the other, doesn't invalidate their clear fascism.  Go back and li

In [ ]:
# Creating a new fine tuning model with 4 epochs
import openai
import os
openai.api_key = os.environ.get("OPENAI_API_KEY")

openai.File.create(
  file=open("train_data.jsonl", "rb"),
  purpose='fine-tune'
)

<File file id=file-tNXtH3bJ4rCC7F1ylgG8z4lp at 0x7cd8957b2200> JSON: {
  "object": "file",
  "id": "file-tNXtH3bJ4rCC7F1ylgG8z4lp",
  "purpose": "fine-tune",
  "filename": "file",
  "bytes": 7647765,
  "created_at": 1693577101,
  "status": "uploaded",
  "status_details": null
}

In [ ]:

# List up to 10 events from a fine-tuning job
openai.FineTuningJob.list_events(id="ftjob-tVW52S3qC5Vfvh5NgYaSSBmW", limit=10)

<OpenAIObject list at 0x7cd88256e2f0> JSON: {
  "object": "list",
  "data": [
    {
      "object": "fine_tuning.job.event",
      "id": "ftevent-WT2md6dC6MQW5bKbfAkDSp4Z",
      "created_at": 1693576313,
      "level": "info",
      "message": "Fine-tuning job successfully completed",
      "data": null,
      "type": "message"
    },
    {
      "object": "fine_tuning.job.event",
      "id": "ftevent-Z6nu64aLAUdVnQcjULN3GXmK",
      "created_at": 1693576312,
      "level": "info",
      "message": "New fine-tuned model created: ft:gpt-3.5-turbo-0613:personal::7tyqtmxH",
      "data": null,
      "type": "message"
    },
    {
      "object": "fine_tuning.job.event",
      "id": "ftevent-eYcSDHiUy2oUETvYfa7qBWC3",
      "created_at": 1693576262,
      "level": "info",
      "message": "Step 1500/1537: training loss=0.04",
      "data": {
        "step": 1500,
        "train_loss": 0.0354250930249691,
        "train_mean_token_accuracy": 0.9885057210922241
      },
      "type": "metri

In [ ]:
openai.FineTuningJob.list_events(id="ftjob-cbubgF9qMnGGqhcuCIWRiSWu", limit=10)

<OpenAIObject list at 0x7cd881e730b0> JSON: {
  "object": "list",
  "data": [
    {
      "object": "fine_tuning.job.event",
      "id": "ftevent-2EcDtqXMiWL7v5CrOC5CEAHb",
      "created_at": 1693541909,
      "level": "info",
      "message": "Fine-tuning job successfully completed",
      "data": null,
      "type": "message"
    },
    {
      "object": "fine_tuning.job.event",
      "id": "ftevent-3KQj0gqCgwJEYxm3OigNSV3S",
      "created_at": 1693541907,
      "level": "info",
      "message": "New fine-tuned model created: ft:gpt-3.5-turbo-0613:personal::7tptzfbo",
      "data": null,
      "type": "message"
    },
    {
      "object": "fine_tuning.job.event",
      "id": "ftevent-e3a7mEjeTTGSOEdUGxDT7ey4",
      "created_at": 1693541773,
      "level": "info",
      "message": "Step 1500/1591: training loss=0.14",
      "data": {
        "step": 1500,
        "train_loss": 0.1366872787475586,
        "train_mean_token_accuracy": 0.9285714030265808
      },
      "type": "metri

In [ ]:
openai.FineTuningJob.create(training_file="file-ks0IQ1oFKSbEsYtqitPIfcTf", model="gpt-3.5-turbo", hyperparameters={"n_epochs": 7})

<FineTuningJob fine_tuning.job id=ftjob-Q4cjZ6Zo4nx34OQQZowxVXzZ at 0x7cd89578f970> JSON: {
  "object": "fine_tuning.job",
  "id": "ftjob-Q4cjZ6Zo4nx34OQQZowxVXzZ",
  "model": "gpt-3.5-turbo-0613",
  "created_at": 1693578094,
  "finished_at": null,
  "fine_tuned_model": null,
  "organization_id": "org-8EdgLmZyodOaLJc4scfYYceO",
  "result_files": [],
  "status": "created",
  "validation_file": null,
  "training_file": "file-ks0IQ1oFKSbEsYtqitPIfcTf",
  "hyperparameters": {
    "n_epochs": 7
  },
  "trained_tokens": null
}

In [ ]:

# List up to 10 events from a fine-tuning job
openai.FineTuningJob.list_events(id="ftjob-Q4cjZ6Zo4nx34OQQZowxVXzZ", limit=10)

<OpenAIObject list at 0x7cd881e2f330> JSON: {
  "object": "list",
  "data": [
    {
      "object": "fine_tuning.job.event",
      "id": "ftevent-cvn8SGfftR1BQi3lWZ5pqFFx",
      "created_at": 1693581705,
      "level": "info",
      "message": "Fine-tuning job successfully completed",
      "data": null,
      "type": "message"
    },
    {
      "object": "fine_tuning.job.event",
      "id": "ftevent-8eiTAhObQw3XOotPWU7L379g",
      "created_at": 1693581704,
      "level": "info",
      "message": "New fine-tuned model created: ft:gpt-3.5-turbo-0613:personal::7u0FrRh3",
      "data": null,
      "type": "message"
    },
    {
      "object": "fine_tuning.job.event",
      "id": "ftevent-Uwlg19CQr19hZNphStDPDpE6",
      "created_at": 1693581640,
      "level": "info",
      "message": "Step 1500/1529: training loss=0.09",
      "data": {
        "step": 1500,
        "train_loss": 0.09497009217739105,
        "train_mean_token_accuracy": 0.9668311476707458
      },
      "type": "metr

In [ ]:
openai.FineTuningJob.retrieve("ftjob-Q4cjZ6Zo4nx34OQQZowxVXzZ")

<FineTuningJob fine_tuning.job id=ftjob-Q4cjZ6Zo4nx34OQQZowxVXzZ at 0x7cd881e2f290> JSON: {
  "object": "fine_tuning.job",
  "id": "ftjob-Q4cjZ6Zo4nx34OQQZowxVXzZ",
  "model": "gpt-3.5-turbo-0613",
  "created_at": 1693578094,
  "finished_at": 1693581702,
  "fine_tuned_model": "ft:gpt-3.5-turbo-0613:personal::7u0FrRh3",
  "organization_id": "org-8EdgLmZyodOaLJc4scfYYceO",
  "result_files": [
    "file-kJJbiO2n5uTfh9GMClScEfF7"
  ],
  "status": "succeeded",
  "validation_file": null,
  "training_file": "file-ks0IQ1oFKSbEsYtqitPIfcTf",
  "hyperparameters": {
    "n_epochs": 7
  },
  "trained_tokens": 9909284
}

In [ ]:
import openai
import json
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score

# Load the validation data
with open("valid_data.jsonl", "r") as f:
    valid_data = [json.loads(line) for line in f]

# Initialize the lists for true labels and predictions
true_labels = []
predicted_labels = []

# Get predictions for each example in validation data
for example in valid_data:
    completion = openai.ChatCompletion.create(
        model="ft:gpt-3.5-turbo-0613:personal::7u0FrRh3",
        messages=[
            {"role": "system", "content": "You are an assistant that is meant to determine whether the comment mentioned in the user message is an example of counterspeech. Counterspeech is defined as a response or comment that counters hateful or harmful speech/ideas. Respond with true or false."},
            {"role": "user", "content": example["messages"][1]["content"]}
        ]
    )

    predicted = completion.choices[0].message["content"].lower()

    # Handle any unexpected output and classify it as "false"
    if predicted not in ["true", "false"]:
        predicted = "false"

    true = example["messages"][2]["content"].lower()

    predicted_labels.append(predicted)
    true_labels.append(true)

# Calculate evaluation metrics
accuracy = accuracy_score(true_labels, predicted_labels)
precision = precision_score(true_labels, predicted_labels, pos_label="true")
recall = recall_score(true_labels, predicted_labels, pos_label="true")
f1 = f1_score(true_labels, predicted_labels, pos_label="true")

# Find which examples were incorrect
incorrect_examples = [example for i, example in enumerate(valid_data) if true_labels[i] != predicted_labels[i]]
correct_examples = [example for i, example in enumerate(valid_data) if true_labels[i] == predicted_labels[i]]

# Print the results
print(f"Accuracy: {accuracy:.2f}")
print(f"Precision: {precision:.2f}")
print(f"Recall: {recall:.2f}")
print(f"F1-score: {f1:.2f}")
print("\nIncorrect Examples:")
for example in incorrect_examples:
    print(example)
print("\nCorrect Examples:")
for example in correct_examples:
    print(example)


Accuracy: 0.85
Precision: 0.85
Recall: 0.84
F1-score: 0.85

Incorrect Examples:
{'messages': [{'role': 'system', 'content': 'You are an assistant that is meant to determine whether the comment mentioned in the user message is an example of counterspeech. Counterspeech is defined as a response or comment that counters hateful or harmful speech/ideas. Respond with true or false.'}, {'role': 'user', 'content': 'A YouTube Video, which contains hateful content that targets the LGBT community, has the following comment: Should be titled "Great preachers"'}, {'role': 'assistant', 'content': 'false'}]}
{'messages': [{'role': 'system', 'content': 'You are an assistant that is meant to determine whether the comment mentioned in the user message is an example of counterspeech. Counterspeech is defined as a response or comment that counters hateful or harmful speech/ideas. Respond with true or false.'}, {'role': 'user', 'content': "A YouTube Video, which contains hateful content that targets the L

In [ ]:
openai.FineTuningJob.create(training_file="file-ks0IQ1oFKSbEsYtqitPIfcTf", model="gpt-3.5-turbo", hyperparameters={"n_epochs": 5})

<FineTuningJob fine_tuning.job id=ftjob-lamu0FylTdsakGFB0uKh2rhu at 0x7cd881e70860> JSON: {
  "object": "fine_tuning.job",
  "id": "ftjob-lamu0FylTdsakGFB0uKh2rhu",
  "model": "gpt-3.5-turbo-0613",
  "created_at": 1693584922,
  "finished_at": null,
  "fine_tuned_model": null,
  "organization_id": "org-8EdgLmZyodOaLJc4scfYYceO",
  "result_files": [],
  "status": "created",
  "validation_file": null,
  "training_file": "file-ks0IQ1oFKSbEsYtqitPIfcTf",
  "hyperparameters": {
    "n_epochs": 5
  },
  "trained_tokens": null
}

In [ ]:
openai.FineTuningJob.retrieve("ftjob-lamu0FylTdsakGFB0uKh2rhu")

<FineTuningJob fine_tuning.job id=ftjob-lamu0FylTdsakGFB0uKh2rhu at 0x7cd881e75170> JSON: {
  "object": "fine_tuning.job",
  "id": "ftjob-lamu0FylTdsakGFB0uKh2rhu",
  "model": "gpt-3.5-turbo-0613",
  "created_at": 1693584922,
  "finished_at": null,
  "fine_tuned_model": null,
  "organization_id": "org-8EdgLmZyodOaLJc4scfYYceO",
  "result_files": [],
  "status": "running",
  "validation_file": null,
  "training_file": "file-ks0IQ1oFKSbEsYtqitPIfcTf",
  "hyperparameters": {
    "n_epochs": 5
  },
  "trained_tokens": null
}

In [ ]:
# List up to 10 events from a fine-tuning job
openai.FineTuningJob.list_events(id="ftjob-lamu0FylTdsakGFB0uKh2rhu", limit=10)

<OpenAIObject list at 0x7cd8957b2250> JSON: {
  "object": "list",
  "data": [
    {
      "object": "fine_tuning.job.event",
      "id": "ftevent-Yic67eJmY3LeFd2ChfyzTzpd",
      "created_at": 1693588933,
      "level": "info",
      "message": "Step 1400/1505: training loss=0.06",
      "data": {
        "step": 1400,
        "train_loss": 0.05946924351155758,
        "train_mean_token_accuracy": 0.9395424723625183
      },
      "type": "metrics"
    },
    {
      "object": "fine_tuning.job.event",
      "id": "ftevent-uwQVKAQogUtE4qUbXOSU7haP",
      "created_at": 1693588686,
      "level": "info",
      "message": "Step 1300/1505: training loss=0.06",
      "data": {
        "step": 1300,
        "train_loss": 0.06191626377403736,
        "train_mean_token_accuracy": 0.9614695310592651
      },
      "type": "metrics"
    },
    {
      "object": "fine_tuning.job.event",
      "id": "ftevent-Sz8dwGo4xE2k6tYPTLVzfs7x",
      "created_at": 1693588440,
      "level": "info",
      "m

In [ ]:
openai.FineTuningJob.retrieve("ftjob-lamu0FylTdsakGFB0uKh2rhu")

<FineTuningJob fine_tuning.job id=ftjob-lamu0FylTdsakGFB0uKh2rhu at 0x7cd881ff8680> JSON: {
  "object": "fine_tuning.job",
  "id": "ftjob-lamu0FylTdsakGFB0uKh2rhu",
  "model": "gpt-3.5-turbo-0613",
  "created_at": 1693584922,
  "finished_at": 1693589197,
  "fine_tuned_model": "ft:gpt-3.5-turbo-0613:personal::7u2Ck87d",
  "organization_id": "org-8EdgLmZyodOaLJc4scfYYceO",
  "result_files": [
    "file-FLnu4hbnkJRAkiHb3HRAeTzp"
  ],
  "status": "succeeded",
  "validation_file": null,
  "training_file": "file-ks0IQ1oFKSbEsYtqitPIfcTf",
  "hyperparameters": {
    "n_epochs": 5
  },
  "trained_tokens": 7078060
}

In [ ]:
import openai
import json
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score

# Load the validation data
with open("valid_data.jsonl", "r") as f:
    valid_data = [json.loads(line) for line in f]

# Initialize the lists for true labels and predictions
true_labels = []
predicted_labels = []

# Get predictions for each example in validation data
for example in valid_data:
    completion = openai.ChatCompletion.create(
        model="ft:gpt-3.5-turbo-0613:personal::7u2Ck87d",
        messages=[
            {"role": "system", "content": "You are an assistant that is meant to determine whether the comment mentioned in the user message is an example of counterspeech. Counterspeech is defined as a response or comment that counters hateful or harmful speech/ideas. Respond with true or false."},
            {"role": "user", "content": example["messages"][1]["content"]}
        ]
    )

    predicted = completion.choices[0].message["content"].lower()

    # Handle any unexpected output and classify it as "false"
    if predicted not in ["true", "false"]:
        predicted = "false"

    true = example["messages"][2]["content"].lower()

    predicted_labels.append(predicted)
    true_labels.append(true)

# Calculate evaluation metrics
accuracy = accuracy_score(true_labels, predicted_labels)
precision = precision_score(true_labels, predicted_labels, pos_label="true")
recall = recall_score(true_labels, predicted_labels, pos_label="true")
f1 = f1_score(true_labels, predicted_labels, pos_label="true")

# Find which examples were incorrect
incorrect_examples = [example for i, example in enumerate(valid_data) if true_labels[i] != predicted_labels[i]]
correct_examples = [example for i, example in enumerate(valid_data) if true_labels[i] == predicted_labels[i]]

# Print the results
print(f"Accuracy: {accuracy:.2f}")
print(f"Precision: {precision:.2f}")
print(f"Recall: {recall:.2f}")
print(f"F1-score: {f1:.2f}")
print("\nIncorrect Examples:")
for example in incorrect_examples:
    print(example)
print("\nCorrect Examples:")
for example in correct_examples:
    print(example)


Accuracy: 0.85
Precision: 0.85
Recall: 0.86
F1-score: 0.85

Incorrect Examples:
{'messages': [{'role': 'system', 'content': 'You are an assistant that is meant to determine whether the comment mentioned in the user message is an example of counterspeech. Counterspeech is defined as a response or comment that counters hateful or harmful speech/ideas. Respond with true or false.'}, {'role': 'user', 'content': 'A YouTube Video, which contains hateful content that targets the LGBT community, has the following comment: shes ignorant because if she read the original scripture n hebrew she would get it but shes fat its a sin for that shes not pure if she was smart what is his personal name tooken out of scripture and u christians say God for its a title and the end of the day many people lose because of false teachings'}, {'role': 'assistant', 'content': 'true'}]}
{'messages': [{'role': 'system', 'content': 'You are an assistant that is meant to determine whether the comment mentioned in the 

In [ ]:
import openai
import json
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score

# Load the validation data
with open("test_data.jsonl", "r") as f:
    valid_data = [json.loads(line) for line in f]

# Initialize the lists for true labels and predictions
true_labels = []
predicted_labels = []

# Get predictions for each example in validation data
for example in valid_data:
    completion = openai.ChatCompletion.create(
        model="ft:gpt-3.5-turbo-0613:personal::7u2Ck87d",
        messages=[
            {"role": "system", "content": "You are an assistant that is meant to determine whether the comment mentioned in the user message is an example of counterspeech. Counterspeech is defined as a response or comment that counters hateful or harmful speech/ideas. Respond with true or false."},
            {"role": "user", "content": example["messages"][1]["content"]}
        ]
    )

    predicted = completion.choices[0].message["content"].lower()

    # Handle any unexpected output and classify it as "false"
    if predicted not in ["true", "false"]:
        predicted = "false"

    true = example["messages"][2]["content"].lower()

    predicted_labels.append(predicted)
    true_labels.append(true)

# Calculate evaluation metrics
accuracy = accuracy_score(true_labels, predicted_labels)
precision = precision_score(true_labels, predicted_labels, pos_label="true")
recall = recall_score(true_labels, predicted_labels, pos_label="true")
f1 = f1_score(true_labels, predicted_labels, pos_label="true")

# Find which examples were incorrect
incorrect_examples = [example for i, example in enumerate(valid_data) if true_labels[i] != predicted_labels[i]]
correct_examples = [example for i, example in enumerate(valid_data) if true_labels[i] == predicted_labels[i]]

# Print the results
print(f"Accuracy: {accuracy:.2f}")
print(f"Precision: {precision:.2f}")
print(f"Recall: {recall:.2f}")
print(f"F1-score: {f1:.2f}")
print("\nIncorrect Examples:")
for example in incorrect_examples:
    print(example)
print("\nCorrect Examples:")
for example in correct_examples:
    print(example)


Accuracy: 0.83
Precision: 0.82
Recall: 0.84
F1-score: 0.83

Incorrect Examples:
{'messages': [{'role': 'system', 'content': 'You are an assistant that is meant to determine whether the comment mentioned in the user message is an example of counterspeech. Counterspeech is defined as a response or comment that counters hateful or harmful speech/ideas. Respond with true or false.'}, {'role': 'user', 'content': "A YouTube Video, which contains hateful content that targets the Jewish community, has the following comment: Ur obviously trolling and Cutting/pasting:\n\n- Muhammad never hated anyone. Quran says theres no religion compulsion. He spread his message through reason and peace.\n- He did not murder. It was a war of self-defense. And the women of the enemy husbands died, so they were willingly taken. They were treated nicely and taken care of. They were freed if wished\n- He never lusted u liar, he was no ordinary man, he was a mercy to mankind\n- Those muslims r wrong, i follow muham